In [1]:
round(500/4)

125

In [2]:
import matplotlib.pyplot as plt
from matplotlib.patches import Rectangle, FancyArrow
from collections import defaultdict
import pandas as pd
import numpy as np

# -----------------------------
# Generate sample data
# -----------------------------
n = 300

feed_ids = np.arange(1, n + 1)
feed_names = [f"Feed Some extra large text {i}" for i in feed_ids]

parent_feed_ids = [0]
for i in range(1, n):
    if np.random.rand() < 0.7:
        parent_feed_ids.append(np.random.randint(0, i + 1))
    else:
        parent_feed_ids.append(0)

df = pd.DataFrame({
    "feed_id": feed_ids,
    "feed_name": feed_names,
    "parent_feed_id": parent_feed_ids
})

# -----------------------------
# Layout configuration
# -----------------------------
BOX_WIDTH = 4.4
BOX_HEIGHT = 2.2
X_GAP = 2.0
Y_GAP = 2.5
ROOT_GAP = 2.0

# -----------------------------
# Build tree structure
# -----------------------------
children = defaultdict(list)
name_map = dict(zip(df.feed_id, df.feed_name))

for _, r in df.iterrows():
    children[r.parent_feed_id].append(r.feed_id)

# -----------------------------
# Recursive layout
# -----------------------------
positions = {}
current_y = 0
lineage_bounds = []   # (top_y, bottom_y, lineage_id)

def layout_subtree(node_id, depth):
    global current_y

    # Layout children first
    for child in children.get(node_id, []):
        layout_subtree(child, depth + 1)

    # Place node
    if node_id not in positions:
        positions[node_id] = (
            depth * (BOX_WIDTH + X_GAP),
            current_y
        )
        current_y -= Y_GAP

    # Center parent over children
    child_ys = [
        positions[c][1]
        for c in children.get(node_id, [])
        if c in positions
    ]
    if child_ys:
        avg_y = sum(child_ys) / len(child_ys)
        positions[node_id] = (
            depth * (BOX_WIDTH + X_GAP),
            avg_y
        )

# -----------------------------
# Layout each root separately
# -----------------------------
roots = children[0]
lineage_id = 1

for root in roots:
    lineage_top = current_y

    layout_subtree(root, 0)

    lineage_bottom = current_y
    lineage_bounds.append((lineage_top, lineage_bottom, lineage_id))
    lineage_id += 1

    current_y -= ROOT_GAP

# -----------------------------
# Plot
# -----------------------------
fig, ax = plt.subplots(figsize=(80, max(10, len(df) * 2)))

# Draw boxes
for fid, (x, y) in positions.items():
    rect = Rectangle(
        (x, y),
        BOX_WIDTH,
        BOX_HEIGHT,
        edgecolor="black",
        facecolor="#D6EAF8",
        linewidth=1.6
    )
    ax.add_patch(rect)

    ax.text(
        x + BOX_WIDTH / 2,
        y + BOX_HEIGHT / 2,
        name_map[fid],
        ha="center",
        va="center",
        fontsize=20,
        fontweight="bold",
        wrap=True
    )

# Draw arrows
for _, r in df.iterrows():
    if r.parent_feed_id != 0:
        px, py = positions[r.parent_feed_id]
        cx, cy = positions[r.feed_id]

        arrow = FancyArrow(
            px + BOX_WIDTH,
            py + BOX_HEIGHT / 2,
            cx - (px + BOX_WIDTH),
            cy - py,
            width=0.03,
            head_width=0.4,
            head_length=0.5,
            length_includes_head=True,
            color="black"
        )
        ax.add_patch(arrow)

# -----------------------------
# Draw lineage separators & labels
# -----------------------------
x_min = -2
x_max = max(x for x, _ in positions.values()) + BOX_WIDTH + 2

for top_y, bottom_y, lid in lineage_bounds:
    y_sep = bottom_y + ROOT_GAP / 2

    # Separator line
    ax.hlines(
        y=y_sep,
        xmin=x_min,
        xmax=x_max,
        colors="gray",
        linestyles="dashed",
        linewidth=2
    )

    # Lineage label
    ax.text(
        x_min + 0.5,
        y_sep + 0.3,
        f"Lineage {lid}",
        fontsize=16,
        fontweight="bold",
        color="gray"
    )

# -----------------------------
# Title & cleanup
# -----------------------------
ax.set_title(
    "SDMF – Feed Flow Diagram",
    fontsize=28,
    fontweight="bold",
    pad=30
)

ax.axis("off")
ax.autoscale_view()
plt.show()
